In [1]:
%matplotlib inline
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import cv2
import matplotlib.image as mpimg
from tqdm import tqdm
from PIL import Image
from sklearn.model_selection import train_test_split
from keras.preprocessing.image import ImageDataGenerator
from efficientnet import EfficientNetB5
from sklearn.metrics import confusion_matrix
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import GridSearchCV
from keras.models import Sequential
from keras.layers import Dense,GlobalAveragePooling2D
from keras.layers import Dropout, GaussianNoise, GaussianDropout
from keras.layers import Flatten, BatchNormalization
from keras.layers.convolutional import Conv2D, SeparableConv2D
from keras.constraints import maxnorm
from keras.layers.convolutional import MaxPooling2D
from keras.utils import np_utils
from keras import backend as K
from keras import regularizers, optimizers
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import EarlyStopping, ModelCheckpoint, CSVLogger
from keras.wrappers.scikit_learn import KerasClassifier
import types

Using TensorFlow backend.


In [2]:
train_df=pd.read_csv('train.csv')

In [3]:
M_train=train_df.shape[0]
train_data=np.empty([M_train,128,128,3])

In [5]:
for i in range(M_train):
    path='train_images\\'+train_df.iloc[i,0]+'.png'
    img=cv2.imread(path)
    img=cv2.resize(img,(128,128))
    train_data[i,:]=img

In [ ]:
M_test=train_df.shape[0]
test_data=np.empty([M_test,128,128,3])

In [ ]:
for i in range(M_test):
    path='train_images\\'+train_df.iloc[i,0]+'.png'
    img=cv2.imread(path)
    img=cv2.resize(img,(128,128))
    test_data[i,:]=img

In [6]:
labels_data=pd.get_dummies(train_df['diagnosis']).values

In [7]:
x_train, x_test, y_train, y_test = train_test_split(train_data, labels_data,test_size=0.2,random_state=262)

In [19]:
 def create_model(dropout_rate=0.2,activation='relu',initalize='uniform',optimizer='Adam'):
    model=Sequential()
    model.add(Conv2D(16,3,input_shape=[128,128,3], activation=activation ,kernel_initializer=initalize))
    model.add(MaxPooling2D(pool_size=(3, 3)))
    model.add(Conv2D(32,3, activation=activation,kernel_initializer=initalize))
    model.add(MaxPooling2D(pool_size=(3, 3)))
    model.add(BatchNormalization())
    model.add(Conv2D(50,3, activation=activation,kernel_initializer=initalize))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())
    model.add(Dropout(dropout_rate))
    model.add(Flatten())
    model.add(Dense(300, activation=activation,kernel_initializer=initalize))
    model.add(BatchNormalization())
    model.add(Dense(100, activation=activation,kernel_initializer=initalize))
    model.add(BatchNormalization())
    model.add(Dense(30, activation=activation,kernel_initializer=initalize))
    model.add(BatchNormalization())
    model.add(Dense(5, activation='softmax'))
    model.compile(loss='categorical_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [9]:
class KerasBatchClassifier(KerasClassifier):

    def fit(self, X, y, **kwargs):

        # taken from keras.wrappers.scikit_learn.KerasClassifier.fit ###################################################
        if self.build_fn is None:
            self.model = self.__call__(**self.filter_sk_params(self.__call__))
        elif not isinstance(self.build_fn, types.FunctionType) and not isinstance(self.build_fn, types.MethodType):
            self.model = self.build_fn(**self.filter_sk_params(self.build_fn.__call__))
        else:
            self.model = self.build_fn(**self.filter_sk_params(self.build_fn))

        loss_name = self.model.loss
        if hasattr(loss_name, '__name__'):
            loss_name = loss_name.__name__

        if loss_name == 'categorical_crossentropy' and len(y.shape) != 2:
            y = to_categorical(y)

        ################################################################################################################

        datagen=ImageDataGenerator(rotation_range=30,zoom_range=0.2,fill_mode='nearest',horizontal_flip=True, vertical_flip=True, rescale=1/255)
        #datagen = ImageDataGenerator(
           # rotation_range=45,
           # width_shift_range=0.2,
           # height_shift_range=0.2,
            #shear_range=0.2,
            #zoom_range=0.2,
            #horizontal_flip=True,
            #fill_mode='nearest'
       # )

        if 'X_val' in kwargs and 'y_val' in kwargs:
            X_val = kwargs['X_val']
            y_val = kwargs['y_val']

            val_gen = ImageDataGenerator(
                horizontal_flip=True
            )
            val_flow = val_gen.flow(X_val, y_val, batch_size=32)
            val_steps = len(X_val) / 32

            early_stopping = EarlyStopping( patience=5, verbose=5, mode="auto")
            model_checkpoint = ModelCheckpoint("results/best_weights.{epoch:02d}-{loss:.5f}.hdf5", verbose=5, save_best_only=True, mode="auto")
        else:
            val_flow = None
            val_steps = None
            early_stopping = EarlyStopping(monitor="acc", patience=3, verbose=5, mode="auto")
            model_checkpoint = ModelCheckpoint("results/best_weights.{epoch:02d}-{loss:.5f}.hdf5", monitor="acc", verbose=5, save_best_only=True, mode="auto")

        callbacks = [early_stopping, model_checkpoint]

        epochs = self.sk_params['epochs'] if 'epochs' in self.sk_params else 100

        self.__history = self.model.fit_generator(
            datagen.flow(X, y, batch_size=32),  
            steps_per_epoch=len(X) / 32,
            validation_data=val_flow, 
            validation_steps=val_steps, 
            epochs=epochs,
            callbacks=callbacks
        )

        return self.__history

    def score(self, X, y, **kwargs):
        kwargs = self.filter_sk_params(Sequential.evaluate, kwargs)

        loss_name = self.model.loss
        if hasattr(loss_name, '__name__'):
            loss_name = loss_name.__name__
        if loss_name == 'categorical_crossentropy' and len(y.shape) != 2:
            y = to_categorical(y)
        outputs = self.model.evaluate(X, y, **kwargs)
        if type(outputs) is not list:
            outputs = [outputs]
        for name, output in zip(self.model.metrics_names, outputs):
            if name == 'acc':
                return output
        raise Exception('The model is not configured to compute accuracy. '
                        'You should pass `metrics=["accuracy"]` to '
                        'the `model.compile()` method.')

    @property
    def history(self):
        return self.__history

In [21]:
model = KerasBatchClassifier(build_fn=create_model, epochs=20)
lrelu = lambda x: tf.keras.activations.relu(x, alpha=0.1)
activation=['relu','tanh','sigmoid',lrelu]
dropout_rate=[0.0,0.2,0.4,0.6,0.8]
initalize=['uniform','normal','he_uniform']
optimizer=['SGD','RMSprop','Adam']
epochs=[50,100,150,200,250,300]
batch_size=[32,64,128,256,512]
param_grid   = dict(dropout_rate=dropout_rate,epochs=epochs,batch_size=batch_size,activation=activation,initalize=initalize,optimizer=optimizer)
grid = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid.fit(train_data,labels_data)

C:\Users\Microsoft\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)


Epoch 1/50
77/76 [==============================] - ETA: 3:49 - loss: 2.1121 - acc: 0.312 - ETA: 2:02 - loss: 2.2590 - acc: 0.234 - ETA: 1:26 - loss: 2.1939 - acc: 0.229 - ETA: 1:08 - loss: 2.1536 - acc: 0.226 - ETA: 57s - loss: 2.0634 - acc: 0.237 - ETA: 49s - loss: 1.9580 - acc: 0.25 - ETA: 44s - loss: 1.9457 - acc: 0.28 - ETA: 40s - loss: 1.8915 - acc: 0.28 - ETA: 36s - loss: 1.8632 - acc: 0.29 - ETA: 34s - loss: 1.8032 - acc: 0.31 - ETA: 32s - loss: 1.7691 - acc: 0.33 - ETA: 30s - loss: 1.7622 - acc: 0.33 - ETA: 28s - loss: 1.7487 - acc: 0.33 - ETA: 27s - loss: 1.7140 - acc: 0.34 - ETA: 25s - loss: 1.6928 - acc: 0.35 - ETA: 24s - loss: 1.6772 - acc: 0.35 - ETA: 23s - loss: 1.6507 - acc: 0.36 - ETA: 22s - loss: 1.6320 - acc: 0.37 - ETA: 21s - loss: 1.6312 - acc: 0.37 - ETA: 21s - loss: 1.6113 - acc: 0.38 - ETA: 20s - loss: 1.6014 - acc: 0.38 - ETA: 19s - loss: 1.5859 - acc: 0.39 - ETA: 19s - loss: 1.5995 - acc: 0.38 - ETA: 18s - loss: 1.5959 - acc: 0.38 - ETA: 18s - loss: 1.5883 - a

77/76 [==============================] - ETA: 22s - loss: 1.1686 - acc: 0.62 - ETA: 22s - loss: 1.1980 - acc: 0.54 - ETA: 22s - loss: 0.9836 - acc: 0.63 - ETA: 22s - loss: 0.9370 - acc: 0.66 - ETA: 21s - loss: 0.9381 - acc: 0.66 - ETA: 21s - loss: 0.9224 - acc: 0.66 - ETA: 21s - loss: 0.9084 - acc: 0.66 - ETA: 20s - loss: 0.8958 - acc: 0.67 - ETA: 20s - loss: 0.8762 - acc: 0.68 - ETA: 20s - loss: 0.8771 - acc: 0.67 - ETA: 19s - loss: 0.8876 - acc: 0.66 - ETA: 19s - loss: 0.8746 - acc: 0.66 - ETA: 19s - loss: 0.8721 - acc: 0.67 - ETA: 19s - loss: 0.8817 - acc: 0.66 - ETA: 18s - loss: 0.8892 - acc: 0.66 - ETA: 18s - loss: 0.9013 - acc: 0.66 - ETA: 18s - loss: 0.9017 - acc: 0.66 - ETA: 17s - loss: 0.9175 - acc: 0.66 - ETA: 17s - loss: 0.9083 - acc: 0.66 - ETA: 17s - loss: 0.9126 - acc: 0.66 - ETA: 16s - loss: 0.9036 - acc: 0.67 - ETA: 16s - loss: 0.8987 - acc: 0.67 - ETA: 16s - loss: 0.9057 - acc: 0.66 - ETA: 16s - loss: 0.9244 - acc: 0.66 - ETA: 15s - loss: 0.9266 - acc: 0.66 - ETA: 15s 

77/76 [==============================] - ETA: 22s - loss: 0.9180 - acc: 0.65 - ETA: 21s - loss: 0.8348 - acc: 0.70 - ETA: 22s - loss: 0.7955 - acc: 0.75 - ETA: 23s - loss: 0.8009 - acc: 0.72 - ETA: 23s - loss: 0.8919 - acc: 0.68 - ETA: 22s - loss: 0.8665 - acc: 0.69 - ETA: 22s - loss: 0.8359 - acc: 0.70 - ETA: 22s - loss: 0.8146 - acc: 0.71 - ETA: 22s - loss: 0.8562 - acc: 0.71 - ETA: 21s - loss: 0.8445 - acc: 0.71 - ETA: 21s - loss: 0.8236 - acc: 0.72 - ETA: 20s - loss: 0.8330 - acc: 0.72 - ETA: 20s - loss: 0.8301 - acc: 0.71 - ETA: 19s - loss: 0.8621 - acc: 0.70 - ETA: 19s - loss: 0.8543 - acc: 0.70 - ETA: 19s - loss: 0.8472 - acc: 0.70 - ETA: 18s - loss: 0.8384 - acc: 0.70 - ETA: 18s - loss: 0.8230 - acc: 0.71 - ETA: 18s - loss: 0.8179 - acc: 0.71 - ETA: 17s - loss: 0.8149 - acc: 0.70 - ETA: 17s - loss: 0.8078 - acc: 0.70 - ETA: 16s - loss: 0.8001 - acc: 0.71 - ETA: 16s - loss: 0.8197 - acc: 0.70 - ETA: 16s - loss: 0.8323 - acc: 0.69 - ETA: 15s - loss: 0.8270 - acc: 0.70 - ETA: 15s 

77/76 [==============================] - ETA: 22s - loss: 0.8084 - acc: 0.68 - ETA: 22s - loss: 0.7232 - acc: 0.73 - ETA: 22s - loss: 0.8424 - acc: 0.68 - ETA: 21s - loss: 0.8519 - acc: 0.68 - ETA: 21s - loss: 0.8357 - acc: 0.68 - ETA: 21s - loss: 0.7992 - acc: 0.69 - ETA: 21s - loss: 0.8510 - acc: 0.67 - ETA: 20s - loss: 0.8543 - acc: 0.66 - ETA: 20s - loss: 0.8481 - acc: 0.67 - ETA: 19s - loss: 0.8304 - acc: 0.69 - ETA: 19s - loss: 0.7974 - acc: 0.70 - ETA: 19s - loss: 0.8145 - acc: 0.69 - ETA: 19s - loss: 0.8133 - acc: 0.69 - ETA: 19s - loss: 0.8018 - acc: 0.70 - ETA: 19s - loss: 0.8021 - acc: 0.70 - ETA: 19s - loss: 0.8029 - acc: 0.69 - ETA: 19s - loss: 0.7927 - acc: 0.70 - ETA: 18s - loss: 0.7925 - acc: 0.69 - ETA: 18s - loss: 0.7977 - acc: 0.69 - ETA: 18s - loss: 0.7892 - acc: 0.70 - ETA: 17s - loss: 0.7933 - acc: 0.70 - ETA: 17s - loss: 0.7869 - acc: 0.71 - ETA: 17s - loss: 0.7898 - acc: 0.71 - ETA: 16s - loss: 0.7916 - acc: 0.71 - ETA: 16s - loss: 0.8041 - acc: 0.70 - ETA: 16s 

...

77/76 [==============================] - ETA: 2:11 - loss: 0.7513 - acc: 0.750 - ETA: 2:09 - loss: 0.8285 - acc: 0.718 - ETA: 2:08 - loss: 0.7740 - acc: 0.739 - ETA: 2:07 - loss: 0.8220 - acc: 0.703 - ETA: 2:08 - loss: 0.8815 - acc: 0.668 - ETA: 2:05 - loss: 0.8689 - acc: 0.666 - ETA: 2:03 - loss: 0.8385 - acc: 0.674 - ETA: 2:01 - loss: 0.8714 - acc: 0.656 - ETA: 1:59 - loss: 0.8264 - acc: 0.680 - ETA: 1:57 - loss: 0.8261 - acc: 0.684 - ETA: 1:55 - loss: 0.8159 - acc: 0.690 - ETA: 1:53 - loss: 0.8214 - acc: 0.695 - ETA: 1:52 - loss: 0.8302 - acc: 0.692 - ETA: 1:51 - loss: 0.8242 - acc: 0.689 - ETA: 1:49 - loss: 0.8052 - acc: 0.700 - ETA: 1:47 - loss: 0.7964 - acc: 0.707 - ETA: 1:45 - loss: 0.7986 - acc: 0.705 - ETA: 1:43 - loss: 0.7931 - acc: 0.708 - ETA: 1:41 - loss: 0.7882 - acc: 0.708 - ETA: 1:40 - loss: 0.7756 - acc: 0.715 - ETA: 1:38 - loss: 0.7800 - acc: 0.715 - ETA: 1:36 - loss: 0.7676 - acc: 0.720 - ETA: 1:35 - loss: 0.7672 - acc: 0.720 - ETA: 1:33 - loss: 0.7677 - acc: 0.717 -

77/76 [==============================] - ETA: 2:11 - loss: 0.8138 - acc: 0.687 - ETA: 2:10 - loss: 0.6517 - acc: 0.750 - ETA: 2:13 - loss: 0.7203 - acc: 0.760 - ETA: 2:10 - loss: 0.7324 - acc: 0.757 - ETA: 2:07 - loss: 0.7305 - acc: 0.743 - ETA: 2:05 - loss: 0.7171 - acc: 0.744 - ETA: 2:03 - loss: 0.7194 - acc: 0.736 - ETA: 2:01 - loss: 0.7103 - acc: 0.742 - ETA: 1:59 - loss: 0.7175 - acc: 0.743 - ETA: 1:56 - loss: 0.7026 - acc: 0.750 - ETA: 1:55 - loss: 0.6952 - acc: 0.755 - ETA: 1:54 - loss: 0.7040 - acc: 0.750 - ETA: 1:52 - loss: 0.6973 - acc: 0.754 - ETA: 1:51 - loss: 0.6955 - acc: 0.754 - ETA: 1:49 - loss: 0.6970 - acc: 0.756 - ETA: 1:47 - loss: 0.7162 - acc: 0.750 - ETA: 1:46 - loss: 0.7100 - acc: 0.751 - ETA: 1:43 - loss: 0.7155 - acc: 0.744 - ETA: 1:40 - loss: 0.7178 - acc: 0.740 - ETA: 1:38 - loss: 0.7312 - acc: 0.732 - ETA: 1:35 - loss: 0.7268 - acc: 0.732 - ETA: 1:33 - loss: 0.7240 - acc: 0.733 - ETA: 1:30 - loss: 0.7239 - acc: 0.735 - ETA: 1:28 - loss: 0.7272 - acc: 0.731 -

77/76 [==============================] - ETA: 2:07 - loss: 0.6800 - acc: 0.781 - ETA: 2:06 - loss: 0.6464 - acc: 0.781 - ETA: 2:05 - loss: 0.6166 - acc: 0.770 - ETA: 2:04 - loss: 0.6631 - acc: 0.765 - ETA: 2:03 - loss: 0.6887 - acc: 0.756 - ETA: 2:01 - loss: 0.6428 - acc: 0.776 - ETA: 2:00 - loss: 0.6334 - acc: 0.776 - ETA: 1:59 - loss: 0.6219 - acc: 0.793 - ETA: 1:58 - loss: 0.6174 - acc: 0.788 - ETA: 1:56 - loss: 0.6236 - acc: 0.790 - ETA: 1:54 - loss: 0.6214 - acc: 0.786 - ETA: 1:52 - loss: 0.6397 - acc: 0.776 - ETA: 1:50 - loss: 0.6365 - acc: 0.776 - ETA: 1:48 - loss: 0.6405 - acc: 0.770 - ETA: 1:46 - loss: 0.6544 - acc: 0.762 - ETA: 1:44 - loss: 0.6676 - acc: 0.755 - ETA: 1:43 - loss: 0.6666 - acc: 0.757 - ETA: 1:41 - loss: 0.6764 - acc: 0.755 - ETA: 1:39 - loss: 0.6716 - acc: 0.756 - ETA: 1:37 - loss: 0.6858 - acc: 0.745 - ETA: 1:36 - loss: 0.6809 - acc: 0.745 - ETA: 1:34 - loss: 0.6719 - acc: 0.751 - ETA: 1:32 - loss: 0.6741 - acc: 0.747 - ETA: 1:30 - loss: 0.6793 - acc: 0.744 -

C:\Users\Microsoft\Anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:528: FutureWarning: From version 0.22, errors during fit will result in a cross validation score of NaN by default. Use error_score='raise' if you want an exception raised or error_score=np.nan to adopt the behavior from version 0.22.
  FutureWarning)


MemoryError: 

In [ ]:
grid_result.best_params_

In [ ]:
grid_result.best_score_

In [ ]:
# run it after subsuitite with the best parameters
history=model.fit_generator(data_aug.flow(train_data, labels_data, batch_size=32),steps_per_epoch=len(x_train) / 32, epochs=150,callbacks=True,validation_data=0.3)

In [ ]:
plt.figure(figsize=(12,5), dpi=100)
plt.subplot(1,1,1)
plt.plot(history.history['loss'], '.-')
plt.plot(history.history['val_loss'], '.-')

plt.plot(history.history['acc'], '.-')
plt.plot(history.history['val_acc'], '.-')

plt.ylabel('loss')
plt.xlabel('epoch')
plt.legend(['loss', 'val_loss', 'acc', 'val_acc'], loc='lower right')
plt.savefig('model.png')
plt.show()

In [ ]:
def quadratic_kappa(actuals, preds, N=5):
    """This function calculates the Quadratic Kappa Metric used for Evaluation in the PetFinder competition
    at Kaggle. It returns the Quadratic Weighted Kappa metric score between the actual and the predicted values 
    of adoption rating."""
    w = np.zeros((N,N))
    O = confusion_matrix(actuals, preds)
    for i in range(len(w)): 
        for j in range(len(w)):
            w[i][j] = float(((i-j)**2)/(N-1)**2)
    
    act_hist=np.zeros([N])
    for item in actuals: 
        act_hist[item]+=1
    
    pred_hist=np.zeros([N])
    for item in preds: 
        pred_hist[item]+=1
                         
    E = np.outer(act_hist, pred_hist);
    E = E/E.sum();
    O = O/O.sum();
       
    num=0
    den=0
    for i in range(len(w)):
        for j in range(len(w)):
            num+=w[i][j]*O[i][j]
            den+=w[i][j]*E[i][j]
    return (1 - (num/den))

In [ ]:
y_pred = model.predict(x_test)
y_pred=y_pred>0.6
y_pred=1*y_pred
quadratic_kappa(y_test.values.argmax(axis=1),y_pred.argmax(axis=1),N=5)

In [ ]:
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
model.save_weights("modelV3.h5")